<a href="https://colab.research.google.com/github/AMF675/Noise-Alert-System/blob/main/DR_using_CNN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from zipfile import ZipFile
with ZipFile('/content/drive/MyDrive/DR DATASET.zip', 'r') as zipObj:

  zipObj.extractall('DR DATASET')

# New Section

In [2]:
pip install split-folders[full]

In [6]:
import splitfolders
input_folder = '/content/DR DATASET/DR DATASET'
splitfolders.ratio(input_folder, output="dataset",
                   seed=42, ratio=(.7, .2, .1),
                   group_prefix=None)

Copying files: 9285 files [00:04, 2044.09 files/s]


In [ ]:
%rm -rf ''

In [7]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [8]:
import os
import numpy as np
import tensorflow as tf
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.preprocessing.image import load_img, img_to_array
from tensorflow.keras.applications import DenseNet121
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Flatten, Conv2D, BatchNormalization, Softmax
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import confusion_matrix, classification_report

In [9]:
train_dir = '/content/dataset/train'
test_dir = '/content/dataset/test'

In [10]:
input_shape = (224, 224, 3) # DenseNet121 input size
num_classes = len(os.listdir(train_dir))
batch_size = 32
epochs = 8

In [11]:
train_datagen = ImageDataGenerator(
rescale=1.0/255.0,
shear_range=0.2,
zoom_range=0.2,
horizontal_flip=True
)

In [12]:
test_datagen = ImageDataGenerator(rescale=1.0/255.0)

In [13]:
#Load train set images
train_generator = train_datagen.flow_from_directory(
train_dir,
target_size=input_shape[:2],
batch_size=batch_size,
class_mode='categorical'
)
# Load test set images
test_generator = test_datagen.flow_from_directory(
test_dir,
target_size=input_shape[:2],
batch_size=batch_size,
class_mode='categorical'
)

Found 6497 images belonging to 9 classes.
Found 933 images belonging to 9 classes.


In [15]:
## Load the pre-trained DenseNet121 model
base_model = DenseNet121(weights='imagenet', include_top=False, input_shape=input_shape)
# Create a new model using the DenseNet121 base
model = Sequential()
model.add(base_model)
model.add(Conv2D(input_shape=input_shape, filters=64, kernel_size=(3, 3),padding='same', activation='relu'))
model.add(BatchNormalization())
model.add(Conv2D(filters=128, kernel_size=(3,3), padding='same', activation='gelu'))
model.add(BatchNormalization())
model.add(Conv2D(filters=256, kernel_size=(3,3), padding='same', activation='relu'))
model.add(BatchNormalization())
model.add(Conv2D(filters=512, kernel_size=(3,3), padding='same', activation='relu'))
model.add(BatchNormalization())
model.add(Flatten())
model.add(Dense(units=4096, activation='relu'))
model.add(Dense(units=4096, activation='relu'))
model.add(Dense(units=num_classes, activation='softmax'))
# Freeze the layers of the DenseNet121 base (optional)
for layer in base_model.layers:
  layer.trainable = False
  # Compile the model
  model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
  # Summary of the model
  model.summary()



29084464/29084464 ━━━━━━━━━━━━━━━━━━━━ 0s 0us/step


/usr/local/lib/python3.10/dist-packages/keras/src/layers/convolutional/base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ densenet121 (Functional)             │ (None, 7, 7, 1024)          │       7,037,504 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ conv2d (Conv2D)                      │ (None, 7, 7, 64)            │         589,888 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization                  │ (None, 7, 7, 64)            │             256 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ conv2d_1 (Conv2D)                    │ (None, 7, 7, 128)           │          73,856 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization_1                │ (None, 7, 7, 128)           │             512 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ conv2d_2 (Conv2D)                    │ (None, 7, 7, 256)           │         295,168 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization_2                │ (None, 7, 7, 256)           │           1,024 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ conv2d_3 (Conv2D)                    │ (None, 7, 7, 512)           │       1,180,160 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization_3                │ (None, 7, 7, 512)           │           2,048 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ flatten (Flatten)                    │ (None, 25088)               │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense (Dense)                        │ (None, 4096)                │     102,764,544 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_1 (Dense)                      │ (None, 4096)                │      16,781,312 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_2 (Dense)                      │ (None, 9)                   │          36,873 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 128,763,145 (491.19 MB)

...

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ densenet121 (Functional)             │ (None, 7, 7, 1024)          │       7,037,504 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ conv2d (Conv2D)                      │ (None, 7, 7, 64)            │         589,888 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization                  │ (None, 7, 7, 64)            │             256 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ conv2d_1 (Conv2D)                    │ (None, 7, 7, 128)           │          73,856 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization_1                │ (None, 7, 7, 128)           │             512 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ conv2d_2 (Conv2D)                    │ (None, 7, 7, 256)           │         295,168 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization_2                │ (None, 7, 7, 256)           │           1,024 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ conv2d_3 (Conv2D)                    │ (None, 7, 7, 512)           │       1,180,160 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization_3                │ (None, 7, 7, 512)           │           2,048 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ flatten (Flatten)                    │ (None, 25088)               │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense (Dense)                        │ (None, 4096)                │     102,764,544 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_1 (Dense)                      │ (None, 4096)                │      16,781,312 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_2 (Dense)                      │ (None, 9)                   │          36,873 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 128,763,145 (491.19 MB)

 Trainable params: 121,723,721 (464.34 MB)

 Non-trainable params: 7,039,424 (26.85 MB)

In [ ]:
hist = model.fit(
train_generator,
steps_per_epoch=train_generator.samples // batch_size,
epochs=epochs,
validation_data=test_generator,
validation_steps=test_generator.samples // batch_size

)
model.save("/content/dataset Dataset/DesNet121P2-1")

Epoch 1/8


/usr/local/lib/python3.10/dist-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:122: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


165/203 ━━━━━━━━━━━━━━━━━━━━ 5:55 9s/step - accuracy: 0.4065 - loss: 5.2967

In [ ]:
def preprocess_input(image_path):
image = load_img(image_path, target_size=input_shape[:2])
image = img_to_array(image)
image = image.reshape((1,) + image.shape)
image /= 255.0
return image

In [ ]:
def predict_single_image(image_path, model):
preprocessed_image = preprocess_input(image_path)
prediction = model.predict(preprocessed_image)
class_index = np.argmax(prediction) # Get the index of the predicted class
class_label = train_generator.class_indices # Dictionary of class indices to class labels
predicted_class = list(class_label.keys())[list(class_label.values()).index(class_index)]
confidence = prediction[0][class_index] * 100.0
return predicted_class, confidence

In [ ]:
image_path = '/content/dataset/test/2. Mild (or early) NPDR/17326_left.jpeg'
predicted_class, confidence = predict_single_image(image_path, model)
print(f"Predicted Class: {predicted_class}, Confidence: {confidence:.2f}%")

In [ ]:
# Plotting the model accuracy
plt.plot(hist.history['accuracy'], label='train_accuracy')
plt.plot(hist.history['val_accuracy'], label='val_accuracy')
plt.xlabel('Epoch')
plt.ylabel('Accuracy')
plt.legend()
plt.title('Model Accuracy')
plt.show()
# Plotting the model loss
plt.plot(hist.history['loss'], label='train_loss')
plt.plot(hist.history['val_loss'], label='val_loss')

plt.xlabel('Epoch')
plt.ylabel('Loss')
plt.legend()
plt.title('Model Loss')
plt.show()

In [ ]:
# Predict the values from the validation dataset
loss, accuracy = model.evaluate_generator(test_generator)
print("Test: accuracy = %f ; loss = %f " % (accuracy, loss))
y_pred = model.predict_generator(test_generator)
y_p = np.argmax(y_pred, axis=1) # Get the class with the highest probability as the predicted class
# Get true labels from the test_generator
y_g = test_generator.classes
confusion_mtx = confusion_matrix(y_g, y_p)
# plot the confusion matrix
f, ax = plt.subplots(figsize=(8, 8))
sns.heatmap(confusion_mtx, annot=True, linewidths=0.01, cmap="Blues", linecolor="gray", fmt='.1f', ax=ax)
plt.xlabel("Predicted Label")
plt.ylabel("True Label")
plt.title("Confusion Matrix")
plt.show()
# Classification Report
print(classification_report(y_g, y_p))